# Service 1

In [1]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.9/231.9 kB 14.6 MB/s eta 0:00:00


In [3]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service1.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated']]
y = df[['cpu_usage_pct', 'memory_usage_pct']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300,0.25,500, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Allocation: {predicted_allocation[0]}")


[I 2025-05-05 07:54:11,874] A new study created in memory with name: no-name-2f5fb5f0-919e-480a-8f08-8c9120295907


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000516 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 07:54:12,339] Trial 0 finished with value: 0.006967766927809789 and parameters: {'n_estimators': 189, 'learning_rate': 0.1295078145300597, 'num_leaves': 136, 'max_depth': 9, 'subsample': 0.722856871219903, 'colsample_bytree': 0.6893773080292174, 'reg_alpha': 0.06727220210618468, 'reg_lambda': 0.07630956260066879}. Best is trial 0 with value: 0.006967766927809789.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000561 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 11.174197
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 07:54:13,140] Trial 1 finished with value: 0.009211957846902017 and parameters: {'n_estimators': 938, 'learning_rate': 0.25131576434807007, 'num_leaves': 114, 'max_depth': 6, 'subsample': 0.6518868036877229, 'colsample_bytree': 0.7017122558409029, 'reg_alpha': 0.8641302650136703, 'reg_lambda': 0.2060493426738712}. Best is trial 0 with value: 0.006967766927809789.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000443 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 07:54:39,121] Trial 28 finished with value: 0.007287531829748877 and parameters: {'n_estimators': 305, 'learning_rate': 0.11961462621680873, 'num_leaves': 54, 'max_depth': 8, 'subsample': 0.6270043191237104, 'colsample_bytree': 0.7677657938850606, 'reg_alpha': 0.15910552617220966, 'reg_lambda': 0.4318521267348566}. Best is trial 15 with value: 0.006338782655840432.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000671 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 50.398963
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-05-05 07:54:40,446] Trial 29 finished with value: 0.007182731191775773 and parameters: {'n_estimators': 545, 'learning_rate': 0.0927785765092736, 'num_leaves': 130, 'max_depth': 8, 'subsample': 0.7183278402402459, 'colsample_bytree': 0.8584123673698905, 'reg_alpha': 0.026564037495590526, 'reg_lambda': 0.7374117918061889}. Best is trial 15 with value: 0.006338782655840432.


Best Parameters: {'n_estimators': 277, 'learning_rate': 0.037789444267885955, 'num_leaves': 142, 'max_depth': 6, 'subsample': 0.7412925932760491, 'colsample_bytree': 0.7632566245867045, 'reg_alpha': 0.2609687919397711, 'reg_lambda': 0.6734744746141902}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000759 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 8500, number of used features: 5
[LightGBM] [Info] Start training from score 50.128218
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

# Service 2

In [4]:
import pandas as pd
import optuna
import numpy as np
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputRegressor
from sklearn.metrics import mean_squared_error

# Load the dataset
df = pd.read_csv("Service2.csv")

# Define input features and target outputs
X = df[['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated']]
y = df[['cpu_allocated', 'memory_allocated']]

# Train-validation-test split: 70% train, 15% val, 15% test
X_train_full, X_temp, y_train_full, y_temp = train_test_split(X, y, test_size=0.30, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.50, random_state=42)

# Define Optuna objective function for LightGBM
def objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 200),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
    }

    model = MultiOutputRegressor(LGBMRegressor(**params, random_state=42))
    model.fit(X_train_full, y_train_full)
    preds = model.predict(X_val)
    mse = mean_squared_error(y_val, preds)
    return mse

# Run Optuna study
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)
best_params = study.best_params
print("Best Parameters:", best_params)

# Retrain model on train + validation data
X_train_combined = pd.concat([X_train_full, X_val])
y_train_combined = pd.concat([y_train_full, y_val])

final_model = MultiOutputRegressor(LGBMRegressor(**best_params, random_state=42))
final_model.fit(X_train_combined, y_train_combined)

# Evaluate on test set
predictions = final_model.predict(X_test)
mse = mean_squared_error(y_test, predictions)
rmse = np.sqrt(mse)
print(f"\nTest MSE: {mse:.4f}")
print(f"Test RMSE: {rmse:.4f}")

# Example: Predicting resource allocation from sample input
sample = pd.DataFrame([[300,0.25, 500, 40, 70]], columns=['latency_ms', 'cpu_usage_pct', 'memory_usage_pct', 'memory_allocated', 'cpu_allocated'])
predicted_allocation = final_model.predict(sample)
print(f"\nSample Input: {sample.to_dict(orient='records')[0]}")
print(f"Predicted CPU, Memory Allocation: {predicted_allocation[0]}")


[I 2025-05-05 07:55:32,260] A new study created in memory with name: no-name-2799d64b-e369-429d-8d43-4d9239db9d56


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000673 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2025-05-05 07:55:34,875] Trial 0 finished with value: 1.162842205943063 and parameters: {'n_estimators': 588, 'learning_rate': 0.21026379109591528, 'num_leaves': 167, 'max_depth': 11, 'subsample': 0.6792451670028062, 'colsample_bytree': 0.7075822496800033, 'reg_alpha': 0.7717525928613478, 'reg_lambda': 0.4389831432778142}. Best is trial 0 with value: 1.162842205943063.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000383 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2025-05-05 07:55:35,620] Trial 1 finished with value: 0.927097441789374 and parameters: {'n_estimators': 319, 'learning_rate': 0.08583359201539402, 'num_leaves': 157, 'max_depth': 14, 'subsample': 0.9730112287997074, 'colsample_bytree': 0.7048243166421397, 'reg_alpha': 0.8778927295786292, 'reg_lambda': 0.06796972009698854}. Best is trial 1 with value: 0.927097441789374.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000361 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2025-05-05 07:56:03,642] Trial 28 finished with value: 0.8850312527316563 and parameters: {'n_estimators': 795, 'learning_rate': 0.02996645671793073, 'num_leaves': 103, 'max_depth': 8, 'subsample': 0.8951372839192496, 'colsample_bytree': 0.6215835795224037, 'reg_alpha': 0.7351373055596481, 'reg_lambda': 0.46175268929966057}. Best is trial 25 with value: 0.8822415924905318.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000365 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 7000, number of used features: 5
[LightGBM] [Info] Start training from score 0.546854
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2025-05-05 07:56:04,701] Trial 29 finished with value: 1.1275747295235459 and parameters: {'n_estimators': 816, 'learning_rate': 0.22262414558802296, 'num_leaves': 115, 'max_depth': 8, 'subsample': 0.90856054364228, 'colsample_bytree': 0.6075513398247201, 'reg_alpha': 0.7455996341659579, 'reg_lambda': 0.43446745712096246}. Best is trial 25 with value: 0.8822415924905318.


Best Parameters: {'n_estimators': 488, 'learning_rate': 0.0313095738423426, 'num_leaves': 79, 'max_depth': 10, 'subsample': 0.8391651882544341, 'colsample_bytree': 0.6725296481802576, 'reg_alpha': 0.6301698113169306, 'reg_lambda': 0.3381840952574359}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000672 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1110
[LightGBM] [Info] Number of data points in the train set: 8500, number of used features: 5
[LightGBM] [Info] Start training from score 0.549234
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp